# License Plate Recognition using TAO LPRNet

Transfer learning is the process of transferring learned features from one application to another. It is a commonly used training technique where you use a model trained on one task and re-train to use it on a different task. 

Train Adapt Optimize (TAO) Toolkit  is a simple and easy-to-use Python based AI toolkit for taking purpose-built AI models and customizing them with users' own data.

<img align="center" src="https://developer.nvidia.com/sites/default/files/akamai/embedded-transfer-learning-toolkit-software-stack-1200x670px.png" width="1080">


## Learning Objectives

In this notebook, you will learn how to leverage the simplicity and convenience of TAO to:

* Take a pretrained baseline18 LPRNet model and train it on the OpenALPR benchmark dataset
* Run Inference on the trained model
* Export the trained model to a .etlt file for deployment to DeepStream
* Run inference on the exported. etlt model to verify deployment using TensorRT

## Table of Contents

This notebook shows an example usecase of LPRNet using Train Adapt Optimize (TAO) Toolkit.

0. [Set up env variables and map drives](#head-0)
1. [Installing the TAO launcher](#head-1)
2. [Prepare dataset and pre-trained model](#head-2)
3. [Provide training specification](#head-3)
4. [Run TAO training](#head-4)
5. [Evaluate trained models](#head-5)
6. [Inferences](#head-6)
7. [Deploy](#head-7)
8. [Verify the deployed model](#head-8)

## 0. Set up env variables and map drives <a class="anchor" id="head-0"></a>

When using the purpose-built pretrained models from NGC, please make sure to set the `$KEY` environment variable to the key as mentioned in the model overview. Failing to do so, can lead to errors when trying to load them as pretrained models.

The following notebook requires the user to set an env variable called the `$LOCAL_PROJECT_DIR` as the path to the users workspace. Please note that the dataset to run this notebook is expected to reside in the `$LOCAL_PROJECT_DIR/data`, while the TAO experiment generated collaterals will be output to `$LOCAL_PROJECT_DIR/lprnet`. More information on how to set up the dataset and the supported steps in the TAO workflow are provided in the subsequent cells.

*Note: Please make sure to remove any stray artifacts/files from the `$USER_EXPERIMENT_DIR` or `$DATA_DOWNLOAD_DIR` paths as mentioned below, that may have been generated from previous experiments. Having checkpoint files etc may interfere with creating a training graph for a new experiment.*


In [1]:
# Setting up env variables for cleaner command line commands.
import os

print("Please replace the variable with your key.")
%env KEY=nvidia_tlt
%env GPU_INDEX=0
%env USER_EXPERIMENT_DIR=/workspace/tao-experiments/my_tao_cv_sample/myLprnet
%env DATA_DOWNLOAD_DIR=/workspace/tao-experiments/myData/lprDataset

# Please define this local project directory that needs to be mapped to the TAO docker session.
# The dataset expected to be present in $LOCAL_PROJECT_DIR/data, while the results for the steps
# in this notebook will be stored at $LOCAL_PROJECT_DIR/lprnet
%env LOCAL_PROJECT_DIR=/home/jeongho/Desktop/workspace/cv_samples_v1.3.0

os.environ["LOCAL_DATA_DIR"] = os.path.join(os.getenv("LOCAL_PROJECT_DIR", os.getcwd()), "myData", "lprDataset")
os.environ["LOCAL_EXPERIMENT_DIR"] = os.path.join(os.getenv("LOCAL_PROJECT_DIR", os.getcwd()), "my_tao_cv_sample", "myLprnet")

# Set this path if you don't run the notebook from the samples directory.
# %env NOTEBOOK_ROOT=/data/tlt-experiments/lprnet
# The sample spec files are present in the same path as the downloaded samples.
os.environ["LOCAL_SPECS_DIR"] = os.path.join(
    os.getenv("NOTEBOOK_ROOT", os.getcwd()),
    "specs"
)
%env SPECS_DIR=/workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs

# Showing list of specification files.
!ls -rlt $LOCAL_SPECS_DIR

Please replace the variable with your key.
env: KEY=nvidia_tlt
env: GPU_INDEX=0
env: USER_EXPERIMENT_DIR=/workspace/tao-experiments/my_tao_cv_sample/myLprnet
env: DATA_DOWNLOAD_DIR=/workspace/tao-experiments/myData/lprDataset
env: LOCAL_PROJECT_DIR=/home/jeongho/Desktop/workspace/cv_samples_v1.3.0
env: SPECS_DIR=/workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs
total 28
-rwxrwxrwx 1 root    root      70  1월  5 10:22  us_lp_characters.txt
-rwxrwxrwx 1 root    root    1272  1월  5 10:22  tutorial_spec.txt
-rwxrwxrwx 1 root    root    1273  1월  5 10:22  tutorial_spec_scratch.txt
-rw-rw-r-- 1 jeongho jeongho  251  1월 25 17:32 'kr_lp_characters copy.txt'
-rwxrwxrwx 1 jeongho jeongho 1308  1월 26 08:50  my_tutorial_spec.txt
-rwxrwxrwx 1 jeongho jeongho 1310  1월 26 08:54  my_spec_scratch.txt
-rw-rw-r-- 1 jeongho jeongho  255  1월 26 17:07  kr_lp_characters.txt


The cell below maps the project directory on your local host to a workspace directory in the TAO docker instance, so that the data and the results are mapped from in and out of the docker. For more information please refer to the [launcher instance](https://docs.nvidia.com/tao/tao-toolkit/tao_launcher.html) in the user guide.

When running this cell on AWS, update the drive_map entry with the dictionary defined below, so that you don't have permission issues when writing data into folders created by the TAO docker.

```json
drive_map = {
    "Mounts": [
            # Mapping the data directory
            {
                "source": os.environ["LOCAL_PROJECT_DIR"],
                "destination": "/workspace/tao-experiments"
            },
            # Mapping the specs directory.
            {
                "source": os.environ["LOCAL_SPECS_DIR"],
                "destination": os.environ["SPECS_DIR"]
            },
        ],
    "DockerOptions": {
        "user": "{}:{}".format(os.getuid(), os.getgid())
    }
}
```

In [2]:
# Mapping up the local directories to the TAO docker.
import json
mounts_file = os.path.expanduser("~/.tao_mounts.json")

# Define the dictionary with the mapped drives
drive_map = {
    "Mounts": [
            # Mapping the data directory
            {
                "source": os.environ["LOCAL_PROJECT_DIR"],
                "destination": "/workspace/tao-experiments"
            },
            # Mapping the specs directory.
            {
                "source": os.environ["LOCAL_SPECS_DIR"],
                "destination": os.environ["SPECS_DIR"]
            },
        ],
    "DockerOptions": {
        "user": "{}:{}".format(os.getuid(), os.getgid())
    }
}

# Writing the mounts file.
with open(mounts_file, "w") as mfile:
    json.dump(drive_map, mfile, indent=4)

In [3]:
!cat ~/.tao_mounts.json

{
    "Mounts": [
        {
            "source": "/home/jeongho/Desktop/workspace/cv_samples_v1.3.0",
            "destination": "/workspace/tao-experiments"
        },
        {
            "source": "/home/jeongho/Desktop/workspace/cv_samples_v1.3.0/my_tao_cv_sample/myLprnet/specs",
            "destination": "/workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs"
        }
    ],
    "DockerOptions": {
        "user": "1000:1000"
    }
}

In [4]:
# Installing the dependencies
import os
os.environ["PROJECT_DIR"] = os.getcwd()
!pip3 install -r $PROJECT_DIR/../../deps/requirements-pip.txt

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


## 1. Installing the TAO launcher <a class="anchor" id="head-1"></a>
The TAO launcher is a python package distributed as a python wheel listed in the `nvidia-pyindex` python index. You may install the launcher by executing the following cell.

Please note that TAO Toolkit recommends users to run the TAO launcher in a virtual env with python 3.6.9. You may follow the instruction in this [page](https://virtualenvwrapper.readthedocs.io/en/latest/install.html) to set up a python virtual env using the `virtualenv` and `virtualenvwrapper` packages. Once you have setup virtualenvwrapper, please set the version of python to be used in the virtual env by using the `VIRTUALENVWRAPPER_PYTHON` variable. You may do so by running

```sh
export VIRTUALENVWRAPPER_PYTHON=/path/to/bin/python3.x
```
where x >= 6 and <= 8

We recommend performing this step first and then launching the notebook from the virtual environment. In addition to installing TAO python package, please make sure of the following software requirements:
* python >=3.6.9 < 3.8.x
* docker-ce > 19.03.5
* docker-API 1.40
* nvidia-container-toolkit > 1.3.0-1
* nvidia-container-runtime > 3.4.0-1
* nvidia-docker2 > 2.5.0-1
* nvidia-driver > 455+

Once you have installed the pre-requisites, please log in to the docker registry nvcr.io by following the command below

```sh
docker login nvcr.io
```

You will be triggered to enter a username and password. The username is `$oauthtoken` and the password is the API key generated from `ngc.nvidia.com`. Please follow the instructions in the [NGC setup guide](https://docs.nvidia.com/ngc/ngc-overview/index.html#generating-api-key) to generate your own API key.

Please note that TAO Toolkit recommends users to run the TAO launcher in a virtual env with python >=3.6.9. You may follow the instruction in this [page](https://virtualenvwrapper.readthedocs.io/en/latest/install.html) to set up a python virtual env using the virtualenv and virtualenvwrapper packages.

In [5]:
# SKIP this step IF you have already installed the TAO launcher.
!pip3 install nvidia-pyindex
!pip3 install nvidia-tao

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [6]:
# View the versions of the TAO launcher
!tao info

Configuration of the TAO Toolkit Instance
dockers: ['nvidia/tao/tao-toolkit-tf', 'nvidia/tao/tao-toolkit-pyt', 'nvidia/tao/tao-toolkit-lm']
format_version: 2.0
toolkit_version: 3.21.11
published_date: 11/08/2021


## 2. Prepare dataset and pre-trained model <a class="anchor" id="head-2"></a>

 We will be using the OpenALPR benchmark dataset for the tutorial. The following script will download the dataset automatically and convert it to the format used by TAO. 

In [7]:
# Create local dir
!mkdir -p $LOCAL_DATA_DIR
!mkdir -p $LOCAL_EXPERIMENT_DIR

In [8]:
# verify
!ls -l $LOCAL_DATA_DIR/
!ls -l $LOCAL_DATA_DIR/train
!ls -l $LOCAL_DATA_DIR/train/image
!ls -l $LOCAL_DATA_DIR/train/label


total 628
drwxrwxr-x  2 jeongho jeongho   4096  1월 26 17:06 clean_data
-rw-rw-r--  1 jeongho jeongho   1694  1월 26 17:05 clean_lpr_dataset.py
drwxrwxr-x 11 jeongho jeongho 548864  1월 26 15:40 data
-rw-rw-r--  1 jeongho jeongho   6218  1월 26 15:58 fetch_data_from_label_studio_2.py
-rw-rw-r--  1 jeongho jeongho   5710  1월 26 11:50 fetch_data_from_label_studio.py
-rw-rw-r--  1 jeongho jeongho   3440  1월 26 16:06 find_error_data.py
-rw-rw-r--  1 jeongho jeongho   1401  1월 26 10:02 studio1.json
-rw-rw-r--  1 jeongho jeongho   1565  1월 26 10:01 studio2.json
-rw-rw-r--  1 jeongho jeongho  27362  1월 26 12:02 studio3.json
-rw-rw-r--  1 jeongho jeongho    198  1월 26 16:05 test2.py
-rw-rw-r--  1 jeongho jeongho   1125  1월 26 11:47 test.py
drwxrwxr-x  4 jeongho jeongho   4096  1월 26 16:32 train
drwxrwxr-x  5 jeongho jeongho   4096  1월 26 09:32 try1
drwxrwxr-x  4 jeongho jeongho   4096  1월 26 17:06 try2
drwxrwxr-x  4 jeongho jeongho   4096  1월 26 16:32 val
total 3676
drwxrwxr-x 2 jeongho jeongho 18

-rw-rw-r-- 1 jeongho jeongho   7751  1월 26 16:32 20210303_212929_24너8710.jpg
-rw-rw-r-- 1 jeongho jeongho   8662  1월 26 16:32 20210303_213122_66러9699.jpg
-rw-rw-r-- 1 jeongho jeongho   8277  1월 26 16:32 20210303_213358_159누8371.jpg
-rw-rw-r-- 1 jeongho jeongho  10022  1월 26 16:32 20210303_213442_35조9528.jpg
-rw-rw-r-- 1 jeongho jeongho   8077  1월 26 16:32 20210303_213621_61소0881.jpg
-rw-rw-r-- 1 jeongho jeongho   7432  1월 26 16:32 20210303_213800_31서1311.jpg
-rw-rw-r-- 1 jeongho jeongho  10704  1월 26 16:32 20210303_214126_168보4508.jpg
-rw-rw-r-- 1 jeongho jeongho   8375  1월 26 16:32 20210303_214137_30구7178.jpg
-rw-rw-r-- 1 jeongho jeongho  11917  1월 26 16:32 20210303_214138_140하6869.jpg
-rw-rw-r-- 1 jeongho jeongho  10914  1월 26 16:32 20210303_214342_52더7129.jpg
-rw-rw-r-- 1 jeongho jeongho   9044  1월 26 16:32 20210303_215030_61구0642.jpg
-rw-rw-r-- 1 jeongho jeongho   5297  1월 26 16:32 20210303_215118_30고5472.jpg
-rw-rw-r-- 1 jeongho jeongho  11088  1월 26 16:32 20210303_215118_30다7752.

-rw-rw-r-- 1 jeongho jeongho   2769  1월 26 16:32 20210309_122541_160하4431.jpg
-rw-rw-r-- 1 jeongho jeongho  10235  1월 26 16:32 20210309_122607_45너6884.jpg
-rw-rw-r-- 1 jeongho jeongho   9602  1월 26 16:32 20210309_122701_59라7724.jpg
-rw-rw-r-- 1 jeongho jeongho   7188  1월 26 16:32 20210309_122816_경기88사9898.jpg
-rw-rw-r-- 1 jeongho jeongho   6859  1월 26 16:32 20210309_122944_29너5382.jpg
-rw-rw-r-- 1 jeongho jeongho   9517  1월 26 16:32 20210309_123018_254조8301.jpg
-rw-rw-r-- 1 jeongho jeongho   6251  1월 26 16:32 20210309_123025_138너7789.jpg
-rw-rw-r-- 1 jeongho jeongho   6179  1월 26 16:32 20210309_123033_08노0969.jpg
-rw-rw-r-- 1 jeongho jeongho   7642  1월 26 16:32 20210309_123125_24너9578.jpg
-rw-rw-r-- 1 jeongho jeongho   5210  1월 26 16:32 20210309_123132_경기88사9898.jpg
-rw-rw-r-- 1 jeongho jeongho   2623  1월 26 16:32 20210309_123148_138너7789.jpg
-rw-rw-r-- 1 jeongho jeongho   7113  1월 26 16:32 20210309_123325_경기88사9898.jpg
-rw-rw-r-- 1 jeongho jeongho   8988  1월 26 16:32 20210309_123545_6

-rw-rw-r-- 1 jeongho jeongho   6813  1월 26 16:32 20210313_203117_39보0626.jpg
-rw-rw-r-- 1 jeongho jeongho  10349  1월 26 16:32 20210313_203205_38노3245.jpg
-rw-rw-r-- 1 jeongho jeongho  10108  1월 26 16:32 20210313_203310_173호8461.jpg
-rw-rw-r-- 1 jeongho jeongho   9636  1월 26 16:32 20210313_203314_149호4203.jpg
-rw-rw-r-- 1 jeongho jeongho   9756  1월 26 16:32 20210313_203340_16저7640.jpg
-rw-rw-r-- 1 jeongho jeongho  10003  1월 26 16:32 20210313_203340_57머0427.jpg
-rw-rw-r-- 1 jeongho jeongho   7067  1월 26 16:32 20210313_203510_151오6451.jpg
-rw-rw-r-- 1 jeongho jeongho   8946  1월 26 16:32 20210313_203516_168러7853.jpg
-rw-rw-r-- 1 jeongho jeongho   9894  1월 26 16:32 20210313_203549_348라1254.jpg
-rw-rw-r-- 1 jeongho jeongho  11714  1월 26 16:32 20210313_203708_138노5290.jpg
-rw-rw-r-- 1 jeongho jeongho   7848  1월 26 16:32 20210313_203946_53우1989.jpg
-rw-rw-r-- 1 jeongho jeongho   9941  1월 26 16:32 20210313_204011_181수5839.jpg
-rw-rw-r-- 1 jeongho jeongho  13077  1월 26 16:32 20210313_204255_226노

-rw-rw-r-- 1 jeongho jeongho   9428  1월 26 16:32 20210825_074448_57가8051.jpg
-rw-rw-r-- 1 jeongho jeongho   9836  1월 26 16:32 20210825_074457_21거0288.jpg
-rw-rw-r-- 1 jeongho jeongho   8811  1월 26 16:32 20210825_074812_56마7652.jpg
-rw-rw-r-- 1 jeongho jeongho   6583  1월 26 16:32 20210825_075002_07수5802.jpg
-rw-rw-r-- 1 jeongho jeongho   9792  1월 26 16:32 20210825_075437_153무6370.jpg
-rw-rw-r-- 1 jeongho jeongho   6378  1월 26 16:32 20210825_075611_25더6591.jpg
-rw-rw-r-- 1 jeongho jeongho   7872  1월 26 16:32 20210825_080444_137조5304.jpg
-rw-rw-r-- 1 jeongho jeongho   8748  1월 26 16:32 20210825_080449_07두6575.jpg
-rw-rw-r-- 1 jeongho jeongho   9367  1월 26 16:32 20210825_080732_222어2249.jpg
-rw-rw-r-- 1 jeongho jeongho   9285  1월 26 16:32 20210825_081107_90다7909.jpg
-rw-rw-r-- 1 jeongho jeongho   8925  1월 26 16:32 20210825_081113_101허3389.jpg
-rw-rw-r-- 1 jeongho jeongho   9459  1월 26 16:32 20210825_081122_260거5631.jpg
-rw-rw-r-- 1 jeongho jeongho  10084  1월 26 16:32 20210825_081136_173호76

total 128048
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_000026_63더3282.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_000545_39마0425.txt
-rw-rw-r-- 1 jeongho jeongho 10  1월 26 16:32 20210301_000550_150허4977.txt
-rw-rw-r-- 1 jeongho jeongho 10  1월 26 16:32 20210301_000559_122호8415.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_005604_18노8460.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_005820_68보8331.txt
-rw-rw-r-- 1 jeongho jeongho 10  1월 26 16:32 20210301_010753_314보4363.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_012404_42버4231.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_013623_60하4186.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_025325_44호9581.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_025538_44호9581.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_040019_27버5248.txt
-rw-rw-r-- 1 jeongho jeongho  9  1월 26 16:32 20210301_041618_55부4316.txt
-rw-rw-r-- 1 jeongho jeongho 10  1월

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## 2.1 Download pretrained model from NGC

We will use NGC CLI to get the pre-trained models. For more details, go to https://ngc.nvidia.com and click the SETUP on the navigation bar.

In [9]:
# Installing NGC CLI on the local machine.
## Download and install
%env CLI=ngccli_cat_linux.zip
!mkdir -p $LOCAL_PROJECT_DIR/ngccli

# Remove any previously existing CLI installations
!rm -rf $LOCAL_PROJECT_DIR/ngccli/*
!wget "https://ngc.nvidia.com/downloads/$CLI" -P $LOCAL_PROJECT_DIR/ngccli
!unzip -u "$LOCAL_PROJECT_DIR/ngccli/$CLI" -d $LOCAL_PROJECT_DIR/ngccli/
!rm $LOCAL_PROJECT_DIR/ngccli/*.zip 
os.environ["PATH"]="{}/ngccli:{}".format(os.getenv("LOCAL_PROJECT_DIR", ""), os.getenv("PATH", ""))

env: CLI=ngccli_cat_linux.zip
--2022-01-26 17:07:21--  https://ngc.nvidia.com/downloads/ngccli_cat_linux.zip
Resolving ngc.nvidia.com (ngc.nvidia.com)... 13.225.134.64, 13.225.134.125, 13.225.134.61, ...
Connecting to ngc.nvidia.com (ngc.nvidia.com)|13.225.134.64|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 30963252 (30M) [application/zip]
Saving to: ‘/home/jeongho/Desktop/workspace/cv_samples_v1.3.0/ngccli/ngccli_cat_linux.zip’

ngccli_cat_linux.zi 100%[===================>]  29.53M  11.2MB/s    in 2.6s    

2022-01-26 17:07:24 (11.2 MB/s) - ‘/home/jeongho/Desktop/workspace/cv_samples_v1.3.0/ngccli/ngccli_cat_linux.zip’ saved [30963252/30963252]

Archive:  /home/jeongho/Desktop/workspace/cv_samples_v1.3.0/ngccli/ngccli_cat_linux.zip
  inflating: /home/jeongho/Desktop/workspace/cv_samples_v1.3.0/ngccli/ngc  
 extracting: /home/jeongho/Desktop/workspace/cv_samples_v1.3.0/ngccli/ngc.md5  


In [10]:
!ngc registry model list nvidia/tao/lprnet:*

+-------+-------+-------+-------+-------+-------+-------+-------+-------+
| Versi | Accur | Epoch | Batch | GPU   | Memor | File  | Statu | Creat |
| on    | acy   | s     | Size  | Model | y Foo | Size  | s     | ed    |
|       |       |       |       |       | tprin |       |       | Date  |
|       |       |       |       |       | t     |       |       |       |
+-------+-------+-------+-------+-------+-------+-------+-------+-------+
| train | 99.67 | 120   | 1     | V100  | 221.1 | 221.0 | UPLOA | Aug   |
| able_ |       |       |       |       |       | 6 MB  | D_COM | 24,   |
| v1.0  |       |       |       |       |       |       | PLETE | 2021  |
| deplo | 99.67 | 120   | 1     | V100  | 110.1 | 110.0 | UPLOA | Aug   |
| yable |       |       |       |       |       | 9 MB  | D_COM | 24,   |
| _v1.0 |       |       |       |       |       |       | PLETE | 2021  |
+-------+-------+-------+-------+-------+-------+-------+-------+-------+


In [11]:
!mkdir -p $LOCAL_EXPERIMENT_DIR/pretrained_lprnet_baseline18/

In [12]:
# Pull pretrained model from NGC
!ngc registry model download-version nvidia/tao/lprnet:trainable_v1.0 --dest $LOCAL_EXPERIMENT_DIR/pretrained_lprnet_baseline18

Downloaded 34.95 MB in 7s, Download speed: 4.99 MB/s                ^C

Terminating, please wait...


In [13]:
print("Check that model is downloaded into dir.")
!ls -l $LOCAL_EXPERIMENT_DIR/pretrained_lprnet_baseline18/lprnet_vtrainable_v1.0

Check that model is downloaded into dir.
total 226384
-rw------- 1 jeongho jeongho       200  1월 25 15:54 ch_lp_characters.txt
-rw------- 1 jeongho jeongho 115963904  1월 25 15:54 ch_lprnet_baseline18_trainable.tlt
-rw------- 1 jeongho jeongho        70  1월 25 15:54 us_lp_characters.txt
-rw------- 1 jeongho jeongho 115832832  1월 25 15:54 us_lprnet_baseline18_trainable.tlt


## 2. Provide training specification <a class="anchor" id="head-2"></a>

* Note the spec $SPEC_DIR/default_sepc.txt is for training on US license plates:
    * the max license plate length is 8;
        * You can change `max_label_length` in `lpr_config` to satisfy your own dataset.
    * the characters of US license plates are: 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, A, B, C, D, E, F, G, H, I, J, K, L, M, N, P, Q, R, S, T, U, V, W, X, Y, Z 
        * You can change `characters_list_file` in `dataset_config` to set your own characters.
        * `characters_list_file` should contain all the characters in dataset. And one character takes one line. 

In [14]:
!cat $LOCAL_SPECS_DIR/my_tutorial_spec.txt

random_seed: 42
lpr_config {
  hidden_units: 512
  max_label_length: 20
  arch: "baseline"
  nlayers: 18 #setting nlayers to be 10 to use baseline10 model
}
training_config {
  batch_size_per_gpu: 32
  num_epochs: 24
  learning_rate {
  soft_start_annealing_schedule {
    min_learning_rate: 1e-6
    max_learning_rate: 1e-5
    soft_start: 0.001
    annealing: 0.5
  }
  }
  regularizer {
    type: L2
    weight: 5e-4
  }
}
eval_config {
  validation_period_during_training: 5
  batch_size: 1
}
augmentation_config {
    output_width: 96
    output_height: 48
    output_channel: 3
    max_rotate_degree: 5
    rotate_prob: 0.5
    gaussian_kernel_size: 5
    gaussian_kernel_size: 7
    gaussian_kernel_size: 15
    blur_prob: 0.5
    reverse_color_prob: 0.5
    keep_original_prob: 0.3
}
dataset_config {
  data_sources: {
    label_directory_path: "/workspace/tao-experiments/myData/lprDataset/train/label"
    image_directory_path: "/workspace/tao-experiments/myData/lprDataset/train/image"
  }

In [15]:
!cat $LOCAL_SPECS_DIR/my_spec_scratch.txt

random_seed: 42
lpr_config {
  hidden_units: 512
  max_label_length: 20
  arch: "baseline"
  nlayers: 18 #setting nlayers to be 10 to use baseline10 model
}
training_config {
  batch_size_per_gpu: 32
  num_epochs: 100
  learning_rate {
  soft_start_annealing_schedule {
    min_learning_rate: 1e-6
    max_learning_rate: 1e-4
    soft_start: 0.001
    annealing: 0.7
  }
  }
  regularizer {
    type: L2
    weight: 5e-4
  }
}
eval_config {
  validation_period_during_training: 5
  batch_size: 1
}
augmentation_config {
    output_width: 96
    output_height: 48
    output_channel: 3
    max_rotate_degree: 5
    rotate_prob: 0.5
    gaussian_kernel_size: 5
    gaussian_kernel_size: 7
    gaussian_kernel_size: 15
    blur_prob: 0.5
    reverse_color_prob: 0.5
    keep_original_prob: 0.3
}
dataset_config {
  data_sources: {
    label_directory_path: "/workspace/tao-experiments/myData/lprDataset/train/label"
    image_directory_path: "/workspace/tao-experiments/myData/lprDataset/train/image"
  

In [16]:
!cat $LOCAL_SPECS_DIR/kr_lp_characters.txt

0
1
2
3
4
5
6
7
8
9
가
나
다
라
마
바
사
아
자
하
거
너
더
러
머
버
서
어
저
허
고
노
도
로
모
보
소
오
조
호
구
누
두
루
무
부
수
우
주
울
경
기
인
천
강
원
충
남
대
전
북
산
광
제
배
크
임
시
장

## 3. Run TAO training <a class="anchor" id="head-3"></a>
* Provide the sample spec file and the output directory location for models
* WARNING: training will take several hours or one day to complete

In [17]:
!mkdir -p $LOCAL_EXPERIMENT_DIR/experiment_dir_unpruned

In [18]:
print("For multi-GPU, change --gpus based on your machine.")
!tao lprnet train --gpus=1 --gpu_index=$GPU_INDEX \
                  -e $SPECS_DIR/my_spec_scratch.txt \
                  -r $USER_EXPERIMENT_DIR/experiment_dir_unpruned \
                  -k $KEY \
                  -m $USER_EXPERIMENT_DIR/pretrained_lprnet_baseline18/lprnet_vtrainable_v1.0/us_lprnet_baseline18_trainable.tlt

For multi-GPU, change --gpus based on your machine.
2022-01-26 17:07:41,103 [INFO] root: Registry: ['nvcr.io']
2022-01-26 17:07:41,144 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-9qrs64tv because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.

2022-01-26 08:07:47,071 [WARNING] tensorflow: From /root/.cache/bazel/_bazel_root/ed34e6d125608f91724fda23656f1726/execroot/ai_infra/bazel-out/k8-fastbuild/bin/magnet/packages/iva/build_wheel.runfiles/ai_infra/iva/lprnet/scripts/train.py:57: The name tf.ConfigProto is deprecated. Please use tf.compat.v1.ConfigProto instead.




Epoch 1/100
   1/1001 [..............................] - ETA: 2:03:04 - loss: 76.9804WARNING:tensorflow:Method (on_train_batch_end) is slow compared to the batch update (0.633868). Check your callbacks.
2022-01-26 08:08:12,267 [WARNING] tensorflow: Method (on_train_batch_end) is slow compared to the batch update (0.633868). Check your callbacks.
1000/1001 [============================>.] - ETA: 0s - loss: 4.36415c584eece368:58:92 [0] NCCL INFO Bootstrap : Using lo:127.0.0.1<0>
5c584eece368:58:92 [0] NCCL INFO NET/Plugin : Plugin load returned 0 : libnccl-net.so: cannot open shared object file: No such file or directory.
5c584eece368:58:92 [0] NCCL INFO NET/IB : No device found.
5c584eece368:58:92 [0] NCCL INFO NET/Socket : Using [0]lo:127.0.0.1<0> [1]eth0:172.17.0.2<0>
5c584eece368:58:92 [0] NCCL INFO Using network Socket
NCCL version 2.9.9+cuda11.3
5c584eece368:58:92 [0] NCCL INFO Channel 00/32 :    0
5c584eece368:58:92 [0] NCCL INFO Channel 01/32 :    0
5c584eece368:58:92 [0] NCCL IN

1001/1001 [==============================] - 111s 111ms/step - loss: 0.2001
Epoch 32/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1977
Epoch 33/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1963
Epoch 34/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1977
Epoch 35/100
1000/1001 [============================>.] - ETA: 0s - loss: 0.1961
Epoch 00035: saving model to /workspace/tao-experiments/my_tao_cv_sample/myLprnet/experiment_dir_unpruned/weights/lprnet_epoch-35.tlt


*******************************************
Accuracy: 9952 / 10228  0.973015252248729
*******************************************


1001/1001 [==============================] - 262s 262ms/step - loss: 0.1960
Epoch 36/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1953
Epoch 37/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1962
Epoch 38/100
1001/1001 [==============================

1000/1001 [============================>.] - ETA: 0s - loss: 0.1742
Epoch 00085: saving model to /workspace/tao-experiments/my_tao_cv_sample/myLprnet/experiment_dir_unpruned/weights/lprnet_epoch-85.tlt


*******************************************
Accuracy: 9969 / 10228  0.974677356276887
*******************************************


1001/1001 [==============================] - 262s 262ms/step - loss: 0.1742
Epoch 86/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1740
Epoch 87/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1743
Epoch 88/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1742
Epoch 89/100
1001/1001 [==============================] - 112s 112ms/step - loss: 0.1739
Epoch 90/100
1000/1001 [============================>.] - ETA: 0s - loss: 0.1737
Epoch 00090: saving model to /workspace/tao-experiments/my_tao_cv_sample/myLprnet/experiment_dir_unpruned/weights/lprnet_epoch-90.tlt


***************

In [19]:
# print("For multi-GPU, change --gpus based on your machine.")
# !tao lprnet train --gpus=1 --gpu_index=$GPU_INDEX \
#                   -e $SPECS_DIR/my_spec_scratch.txt \
#                   -r $USER_EXPERIMENT_DIR/experiment_dir_unpruned \
#                   -k $KEY \
#                   -m $USER_EXPERIMENT_DIR/pretrained_lprnet_baseline18/lprnet_vtrainable_v1.0/us_lprnet_baseline18_trainable.tlt

For multi-GPU, change --gpus based on your machine.
2022-01-26 21:05:01,778 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:05:01,816 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-7arnpinv because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.

2022-01-26 12:05:06,235 [WARNING] tensorflow: From /root/.cache/bazel/_bazel_root/ed34e6d125608f91724fda23656f1726/execroot/ai_infra/bazel-out/k8-fastbuild/bin/magnet/packages/iva/build_wheel.runfiles/ai_infra/iva/lprnet/scripts/train.py:57: The name tf.ConfigProto is deprecated. Please use tf.compat.v1.ConfigProto instead.




Epoch 1/100
   1/1001 [..............................] - ETA: 1:47:04 - loss: 88.5448WARNING:tensorflow:Method (on_train_batch_end) is slow compared to the batch update (0.660149). Check your callbacks.
2022-01-26 12:05:29,458 [WARNING] tensorflow: Method (on_train_batch_end) is slow compared to the batch update (0.660149). Check your callbacks.
1000/1001 [============================>.] - ETA: 0s - loss: 4.9947fa229024e831:59:93 [0] NCCL INFO Bootstrap : Using lo:127.0.0.1<0>
fa229024e831:59:93 [0] NCCL INFO NET/Plugin : Plugin load returned 0 : libnccl-net.so: cannot open shared object file: No such file or directory.
fa229024e831:59:93 [0] NCCL INFO NET/IB : No device found.
fa229024e831:59:93 [0] NCCL INFO NET/Socket : Using [0]lo:127.0.0.1<0> [1]eth0:172.17.0.2<0>
fa229024e831:59:93 [0] NCCL INFO Using network Socket
NCCL version 2.9.9+cuda11.3
fa229024e831:59:93 [0] NCCL INFO Channel 00/32 :    0
fa229024e831:59:93 [0] NCCL INFO Channel 01/32 :    0
fa229024e831:59:93 [0] NCCL IN

In [20]:
# print("For multi-GPU, change --gpus based on your machine.")
# !tao lprnet train --gpus=1 --gpu_index=$GPU_INDEX \
#                   -e $SPECS_DIR/my_spec_scratch.txt \
#                   -r $USER_EXPERIMENT_DIR/experiment_dir_unpruned \
#                   -k $KEY

In [21]:
print("To resume training from a checkpoint, set the -m option to be the .tlt you want to resume from and --initial_epochs to be the epoch index of the resumed checkpoint")
# !tao lprnet train --gpu_index=$GPU_INDEX \
#                   -e $SPECS_DIR/tutorial_spec.txt \
#                   -r $USER_EXPERIMENT_DIR/experiment_dir_unpruned \
#                   -k $KEY \
#                   -m $USER_EXPERIMENT_DIR/experiment_dir_unpruned/weights/lprnet_epoch-01.tlt
#                   --initial_epoch 2

To resume training from a checkpoint, set the -m option to be the .tlt you want to resume from and --initial_epochs to be the epoch index of the resumed checkpoint


In [22]:
print('Model for each epoch:')
print('---------------------')
!ls -ltrh $LOCAL_EXPERIMENT_DIR/experiment_dir_unpruned/weights/

Model for each epoch:
---------------------
total 2.3G
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 08:50 lprnet_epoch-24.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 17:29 lprnet_epoch-10.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 17:41 lprnet_epoch-15.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 17:53 lprnet_epoch-20.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 18:05 lprnet_epoch-25.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 18:16 lprnet_epoch-30.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 18:28 lprnet_epoch-35.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 18:40 lprnet_epoch-40.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 18:52 lprnet_epoch-45.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 19:04 lprnet_epoch-50.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 19:15 lprnet_epoch-55.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 19:27 lprnet_epoch-60.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 19:39 lprnet_epoch-65.tlt
-rw-r--r-- 1 jeongho jeongho 111M  1월 26 19:51 lprnet_epoch-70.tlt
-rw-r--

## 4. Evaluate trained models <a class="anchor" id="head-4"></a>

In [23]:
!tao lprnet evaluate --gpu_index=$GPU_INDEX -e $SPECS_DIR/my_spec_scratch.txt \
                     -m $USER_EXPERIMENT_DIR/experiment_dir_unpruned/weights/lprnet_epoch-100.tlt \
                     -k $KEY

2022-01-26 21:25:16,951 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:25:16,995 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-vhns6xgi because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.
2022-01-26 12:25:21,540 [INFO] iva.lprnet.utils.spec_loader: Merging specification from /workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs/my_spec_scratch.txt
Using TLT model for inference, setting batch size to the one in eval_config: 1
Producing predictions: 100%|██████████████| 10228/10228 [02:41<00:00, 63.46it/s]
Accuracy: 9971 / 10228  0.9748728979272585
2022-01-26 

## 5. Inferences <a class="anchor" id="head-5"></a>
In this section, we run the lprnet inference tool to generate inferences on the trained models and print the results. 

In [24]:
# Running inference for detection on n images
!tao lprnet inference --gpu_index=$GPU_INDEX -i $DATA_DOWNLOAD_DIR/val/image \
                      -e $SPECS_DIR/my_spec_scratch.txt \
                      -m $USER_EXPERIMENT_DIR/experiment_dir_unpruned/weights/lprnet_epoch-100.tlt \
                      -k $KEY 

2022-01-26 21:28:19,068 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:28:19,108 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-nt1wlsvu because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.
2022-01-26 12:28:23,566 [INFO] iva.lprnet.utils.spec_loader: Merging specification from /workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs/my_spec_scratch.txt
Using TLT model for inference, setting batch size to the one in eval_config: 1
/workspace/tao-experiments/myData/lprDataset/val/image/20210902_143909_324라4549.jpg:324라4549 
/workspace/tao-experiments/myData/lprData

/workspace/tao-experiments/myData/lprDataset/val/image/20210910_232548_14나0351.jpg:14나0351 
/workspace/tao-experiments/myData/lprDataset/val/image/20210903_130430_42호4446.jpg:42호4446 
/workspace/tao-experiments/myData/lprDataset/val/image/20210906_084719_51더8260.jpg:51더8260 
/workspace/tao-experiments/myData/lprDataset/val/image/20210804_101603_02부5351.jpg:02부5351 
/workspace/tao-experiments/myData/lprDataset/val/image/20210809_072714_51더8260.jpg:51더8260 
/workspace/tao-experiments/myData/lprDataset/val/image/20210829_182501_53러4559.jpg:53러4559 
/workspace/tao-experiments/myData/lprDataset/val/image/20210825_101555_51우3415.jpg:51우3415 
/workspace/tao-experiments/myData/lprDataset/val/image/20210830_191747_149하2610.jpg:149하2610 
/workspace/tao-experiments/myData/lprDataset/val/image/20210914_152949_09부0384.jpg:09부0384 
/workspace/tao-experiments/myData/lprDataset/val/image/20210903_175111_85부3140.jpg:85부3140 
/workspace/tao-experiments/myData/lprDataset/val/image/20210810_101209_168주843

/workspace/tao-experiments/myData/lprDataset/val/image/20210823_102722_40누2092.jpg:40누2092 
/workspace/tao-experiments/myData/lprDataset/val/image/20210909_063255_43조7654.jpg:43조7654 
/workspace/tao-experiments/myData/lprDataset/val/image/20210906_135453_49하3568.jpg:49하3568 
/workspace/tao-experiments/myData/lprDataset/val/image/20210913_143834_262누5818.jpg:262누5818 
/workspace/tao-experiments/myData/lprDataset/val/image/20210812_103432_06오5314.jpg:06오5314 
/workspace/tao-experiments/myData/lprDataset/val/image/20210909_164851_52하3351.jpg:52하3351 
/workspace/tao-experiments/myData/lprDataset/val/image/20210813_235123_11러7134.jpg:11러7134 
/workspace/tao-experiments/myData/lprDataset/val/image/20210903_171655_170하2269.jpg:170하2269 
/workspace/tao-experiments/myData/lprDataset/val/image/20210914_140627_45마0383.jpg:45마0383 
/workspace/tao-experiments/myData/lprDataset/val/image/20210908_200539_339수4824.jpg:339수4824 
/workspace/tao-experiments/myData/lprDataset/val/image/20210821_202045_65도

/workspace/tao-experiments/myData/lprDataset/val/image/20210902_133951_393머3114.jpg:393머3114 
/workspace/tao-experiments/myData/lprDataset/val/image/20210804_161516_10도5885.jpg:10도5885 
/workspace/tao-experiments/myData/lprDataset/val/image/20210916_153119_11보8364.jpg:11루8364 
/workspace/tao-experiments/myData/lprDataset/val/image/20210816_202642_03도8555.jpg:03도8555 
/workspace/tao-experiments/myData/lprDataset/val/image/20210917_134108_83버5052.jpg:83버5052 
/workspace/tao-experiments/myData/lprDataset/val/image/20210814_160254_01가5262.jpg:01가5262 
/workspace/tao-experiments/myData/lprDataset/val/image/20210901_123404_101호5640.jpg:101호5640 
/workspace/tao-experiments/myData/lprDataset/val/image/20210912_174727_21너4889.jpg:21너4889 
/workspace/tao-experiments/myData/lprDataset/val/image/20210824_125959_182호5248.jpg:182호5248 
/workspace/tao-experiments/myData/lprDataset/val/image/20210808_115058_149호4757.jpg:149호4757 
/workspace/tao-experiments/myData/lprDataset/val/image/20210807_074452_4

/workspace/tao-experiments/myData/lprDataset/val/image/20210904_213736_28마6726.jpg:28마6726 
/workspace/tao-experiments/myData/lprDataset/val/image/20210912_114208_29머6139.jpg:29머6139 
/workspace/tao-experiments/myData/lprDataset/val/image/20210911_124945_41마5325.jpg:41마5325 
/workspace/tao-experiments/myData/lprDataset/val/image/20210825_013223_69모1369.jpg:69모1369 
/workspace/tao-experiments/myData/lprDataset/val/image/20210812_124916_32라8077.jpg:32라8077 
/workspace/tao-experiments/myData/lprDataset/val/image/20210823_121714_10도5885.jpg:10도5885 
/workspace/tao-experiments/myData/lprDataset/val/image/20210804_171332_10구5976.jpg:10구5976 
/workspace/tao-experiments/myData/lprDataset/val/image/20210804_180745_54조8913.jpg:54조8913 
/workspace/tao-experiments/myData/lprDataset/val/image/20210829_180031_15라1559.jpg:15러1559 
/workspace/tao-experiments/myData/lprDataset/val/image/20210823_203716_57루6534.jpg:57루6534 
/workspace/tao-experiments/myData/lprDataset/val/image/20210915_150123_41모4262.j

...

/workspace/tao-experiments/myData/lprDataset/val/image/20210917_194019_248로1000.jpg:248로1000 
/workspace/tao-experiments/myData/lprDataset/val/image/20210917_165158_266어3024.jpg:266어3024 
/workspace/tao-experiments/myData/lprDataset/val/image/20210917_104433_서울80배1523.jpg:서울80배1523 
/workspace/tao-experiments/myData/lprDataset/val/image/20210911_123331_15거0772.jpg:15거0772 
/workspace/tao-experiments/myData/lprDataset/val/image/20210901_115540_33머5544.jpg:33머5544 
/workspace/tao-experiments/myData/lprDataset/val/image/20210902_144527_245도5599.jpg:245도5599 
/workspace/tao-experiments/myData/lprDataset/val/image/20210905_173240_53소4384.jpg:53소4384 
/workspace/tao-experiments/myData/lprDataset/val/image/20210904_084200_33호6586.jpg:33호6586 
/workspace/tao-experiments/myData/lprDataset/val/image/20210901_232257_12누3919.jpg:12누3919 
/workspace/tao-experiments/myData/lprDataset/val/image/20210801_012847_25노0966.jpg:25노0966 
/workspace/tao-experiments/myData/lprDataset/val/image/20210916_105044

/workspace/tao-experiments/myData/lprDataset/val/image/20210821_131206_354누9867.jpg:354누9867 
/workspace/tao-experiments/myData/lprDataset/val/image/20210906_182610_42나4646.jpg:42나4646 
/workspace/tao-experiments/myData/lprDataset/val/image/20210829_132920_13부1594.jpg:13부1594 
/workspace/tao-experiments/myData/lprDataset/val/image/20210804_072238_66부4655.jpg:66부4655 
/workspace/tao-experiments/myData/lprDataset/val/image/20210904_112714_181우7872.jpg:181우7872 
/workspace/tao-experiments/myData/lprDataset/val/image/20210815_155141_84거0476.jpg:84거0476 
/workspace/tao-experiments/myData/lprDataset/val/image/20210810_084411_43모7729.jpg:43모7729 
/workspace/tao-experiments/myData/lprDataset/val/image/20210917_162548_34두8514.jpg:34두8514 
/workspace/tao-experiments/myData/lprDataset/val/image/20210908_125805_55너6207.jpg:55너6207 
/workspace/tao-experiments/myData/lprDataset/val/image/20210811_181149_22저5904.jpg:22저5904 
/workspace/tao-experiments/myData/lprDataset/val/image/20210903_182840_292서4

/workspace/tao-experiments/myData/lprDataset/val/image/20210813_170617_58가1031.jpg:58가1031 
/workspace/tao-experiments/myData/lprDataset/val/image/20210811_125101_10가1929.jpg:10가1929 
/workspace/tao-experiments/myData/lprDataset/val/image/20210910_144424_81루1220.jpg:81루1220 
/workspace/tao-experiments/myData/lprDataset/val/image/20210906_100818_64루8925.jpg:64루8925 
/workspace/tao-experiments/myData/lprDataset/val/image/20210909_154024_14루9407.jpg:14루9407 
/workspace/tao-experiments/myData/lprDataset/val/image/20210810_150322_04두6634.jpg:04두6634 
/workspace/tao-experiments/myData/lprDataset/val/image/20210802_092712_10가1929.jpg:10가1929 
/workspace/tao-experiments/myData/lprDataset/val/image/20210902_152622_120거4103.jpg:120거4103 
/workspace/tao-experiments/myData/lprDataset/val/image/20210910_190110_31더5393.jpg:31더5393 
/workspace/tao-experiments/myData/lprDataset/val/image/20210810_123334_61거7067.jpg:61거7067 
/workspace/tao-experiments/myData/lprDataset/val/image/20210915_091816_78다1077

/workspace/tao-experiments/myData/lprDataset/val/image/20210916_090235_142두1586.jpg:142두1586 
/workspace/tao-experiments/myData/lprDataset/val/image/20210907_144550_68더1910.jpg:68더1910 
/workspace/tao-experiments/myData/lprDataset/val/image/20210805_163521_25노0966.jpg:25노0966 
/workspace/tao-experiments/myData/lprDataset/val/image/20210803_162721_146하4213.jpg:146하4213 
/workspace/tao-experiments/myData/lprDataset/val/image/20210829_152953_59무2428.jpg:59무2428 
/workspace/tao-experiments/myData/lprDataset/val/image/20210913_123636_342무1373.jpg:342무1373 
/workspace/tao-experiments/myData/lprDataset/val/image/20210913_153038_20주3621.jpg:20주3621 
/workspace/tao-experiments/myData/lprDataset/val/image/20210902_144901_18다7692.jpg:18다7692 
/workspace/tao-experiments/myData/lprDataset/val/image/20210908_173522_49부4597.jpg:49부4597 
/workspace/tao-experiments/myData/lprDataset/val/image/20210805_195810_63두2455.jpg:63두2455 
/workspace/tao-experiments/myData/lprDataset/val/image/20210906_135902_365

/workspace/tao-experiments/myData/lprDataset/val/image/20210901_163616_03도8555.jpg:03도8555 
/workspace/tao-experiments/myData/lprDataset/val/image/20210828_135808_69루4345.jpg:69루4345 
/workspace/tao-experiments/myData/lprDataset/val/image/20210818_112500_36라7574.jpg:467574 
/workspace/tao-experiments/myData/lprDataset/val/image/20210908_184207_249조9989.jpg:249조9989 
/workspace/tao-experiments/myData/lprDataset/val/image/20210908_103414_66서7927.jpg:66서7927 
/workspace/tao-experiments/myData/lprDataset/val/image/20210906_061519_43조7654.jpg:43조7654 
/workspace/tao-experiments/myData/lprDataset/val/image/20210821_121123_01가5262.jpg:01가5262 
/workspace/tao-experiments/myData/lprDataset/val/image/20210908_115524_22저5904.jpg:22저5904 
/workspace/tao-experiments/myData/lprDataset/val/image/20210901_184434_10도5885.jpg:10도5885 
/workspace/tao-experiments/myData/lprDataset/val/image/20210915_103834_10서4875.jpg:10서4875 
/workspace/tao-experiments/myData/lprDataset/val/image/20210916_215735_39하0390.

## 6. Deploy! <a class="anchor" id="head-6"></a>

In [25]:
# Export in FP32 mode. 
!mkdir -p $LOCAL_EXPERIMENT_DIR/export 
!tao lprnet export --gpu_index=$GPU_INDEX -m $USER_EXPERIMENT_DIR/experiment_dir_unpruned/weights/lprnet_epoch-100.tlt \
                   -k $KEY \
                   -e $SPECS_DIR/my_spec_scratch.txt \
                   -o $USER_EXPERIMENT_DIR/export/lprnet_epoch-100.etlt \
                   --data_type fp32 \
                   --engine_file $USER_EXPERIMENT_DIR/export/lprnet_epoch-100.engine

2022-01-26 21:31:28,190 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:31:28,232 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-zyilp9b7 because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.
Traceback (most recent call last):
  File "/root/.cache/bazel/_bazel_root/ed34e6d125608f91724fda23656f1726/execroot/ai_infra/bazel-out/k8-fastbuild/bin/magnet/packages/iva/build_wheel.runfiles/ai_infra/iva/lprnet/scripts/export.py", line 216, in <module>
  File "/root/.cache/bazel/_bazel_root/ed34e6d125608f91724fda23656f1726/execroot/ai_infra/bazel-out/k8-fastbuild/bin/magnet/pa

In [26]:
# Verify the tensorrt engine accuracy on the validation dataset
!tao lprnet evaluate --gpu_index=$GPU_INDEX -e $SPECS_DIR/my_spec_scratch.txt \
                     -m $USER_EXPERIMENT_DIR/export/lprnet_epoch-100.engine \
                     --trt

2022-01-26 21:31:44,015 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:31:44,052 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-lu_o5k18 because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.
2022-01-26 12:31:48,406 [INFO] iva.lprnet.utils.spec_loader: Merging specification from /workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs/my_spec_scratch.txt
Using TRT engine for inference, setting batch size to the one in eval_config: 1
Producing predictions:   0%|                          | 0/10228 [00:00<?, ?it/s]Traceback (most recent call last):
  File "/root/.cach

In [27]:
# Check if etlt model is correctly saved.
!ls -l $LOCAL_EXPERIMENT_DIR/export

total 400996
-rw-r--r-- 1 jeongho jeongho 53075453  1월 26 09:00 lprnet_epoch-100_dynamic_batch.engine
-rw-r--r-- 1 jeongho jeongho 94486436  1월 26 08:58 lprnet_epoch-100.engine
-rw-r--r-- 1 jeongho jeongho 57809049  1월 26 08:58 lprnet_epoch-100.etlt
-rw-r--r-- 1 jeongho jeongho 53046083  1월 25 17:48 lprnet_epoch-24_dynamic_batch.engine
-rw-r--r-- 1 jeongho jeongho 94435753  1월 25 17:46 lprnet_epoch-24.engine
-rw-r--r-- 1 jeongho jeongho 57757749  1월 25 17:46 lprnet_epoch-24.etlt


Verify engine generation using the `tao-converter` utility included with the docker.

The `tao-converter` produces optimized tensorrt engines for the platform that it resides on. Therefore, to get maximum performance, please instantiate this docker and execute the `tao-converter` command, with the exported `.etlt` file and calibration cache (for int8 mode) on your target device. The tao-converter utility included in this docker only works for x86 devices, with discrete NVIDIA GPU's. 

For the jetson devices, please download the tao-converter for jetson from the dev zone link [here](https://developer.nvidia.com/tao-converter). 

If you choose to integrate your model into deepstream directly, please refer to [deepstream dev guide](https://docs.nvidia.com/metropolis/deepstream/dev-guide/index.html) for more details.

In [28]:
print('Exported model:')
print('------------')
!ls -lth $LOCAL_EXPERIMENT_DIR/export

Exported model:
------------
total 392M
-rw-r--r-- 1 jeongho jeongho 51M  1월 26 09:00 lprnet_epoch-100_dynamic_batch.engine
-rw-r--r-- 1 jeongho jeongho 91M  1월 26 08:58 lprnet_epoch-100.engine
-rw-r--r-- 1 jeongho jeongho 56M  1월 26 08:58 lprnet_epoch-100.etlt
-rw-r--r-- 1 jeongho jeongho 51M  1월 25 17:48 lprnet_epoch-24_dynamic_batch.engine
-rw-r--r-- 1 jeongho jeongho 91M  1월 25 17:46 lprnet_epoch-24.engine
-rw-r--r-- 1 jeongho jeongho 56M  1월 25 17:46 lprnet_epoch-24.etlt


In [29]:
# Convert to TensorRT engine(FP16).
# Please use -p option to set the min_shape / opt_shape / max_shape for dynmaic batch engine.
!tao converter $USER_EXPERIMENT_DIR/export/lprnet_epoch-100.etlt \
                   -k $KEY \
                   -p image_input,1x3x48x96,4x3x48x96,16x3x48x96 \
                   -t fp16 \
                   -e $USER_EXPERIMENT_DIR/export/lprnet_epoch-100_dynamic_batch.engine

2022-01-26 21:32:01,856 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:32:01,892 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
[INFO] [MemUsageChange] Init CUDA: CPU +332, GPU +0, now: CPU 338, GPU 977 (MiB)
[INFO] ----------------------------------------------------------------
[INFO] Input filename:   /tmp/filedDej4u
[INFO] ONNX IR version:  0.0.7
[INFO] Opset version:    13
[INFO] Producer name:    keras2onnx
[INFO] Producer version: 1.8.1
[INFO] Domain:           onnxmltools
[INFO] Model version:    0
[INFO] Doc string:       
[INFO] ----------------------------------------------------------------
[WARNING] /trt_oss_src/TensorRT/parsers/onnx/onnx2trt_utils.cpp:364: Your ONNX model has been generated with INT64 weights, while TensorRT does not natively support INT64. Attempting to cast down to INT32.
[WARNING] /trt_oss_src/TensorRT/parsers/onnx/ShapedWeights.cpp:172: Weights td_dense/ker

In [30]:
print('Exported engine:')
print('------------')
!ls -lh $LOCAL_EXPERIMENT_DIR/export/

Exported engine:
------------
total 392M
-rw-r--r-- 1 jeongho jeongho 51M  1월 26 21:33 lprnet_epoch-100_dynamic_batch.engine
-rw-r--r-- 1 jeongho jeongho 91M  1월 26 08:58 lprnet_epoch-100.engine
-rw-r--r-- 1 jeongho jeongho 56M  1월 26 08:58 lprnet_epoch-100.etlt
-rw-r--r-- 1 jeongho jeongho 51M  1월 25 17:48 lprnet_epoch-24_dynamic_batch.engine
-rw-r--r-- 1 jeongho jeongho 91M  1월 25 17:46 lprnet_epoch-24.engine
-rw-r--r-- 1 jeongho jeongho 56M  1월 25 17:46 lprnet_epoch-24.etlt


## 7. Verify the deployed model <a class="anchor" id="head-7"></a>

Verify the converted engine.

In [31]:
# Running evaluation on validation dataset
!tao lprnet evaluate  --gpu_index=$GPU_INDEX -e $SPECS_DIR/my_spec_scratch.txt \
                      -m $USER_EXPERIMENT_DIR/export/lprnet_epoch-100_dynamic_batch.engine \
                      --trt        

2022-01-26 21:33:49,512 [INFO] root: Registry: ['nvcr.io']
2022-01-26 21:33:49,551 [INFO] tlt.components.instance_handler.local_instance: Running command in container: nvcr.io/nvidia/tao/tao-toolkit-tf:v3.21.11-tf1.15.5-py3
Matplotlib created a temporary config/cache directory at /tmp/matplotlib-7u5ngcz5 because the default path (/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.
Using TensorFlow backend.
Using TensorFlow backend.
2022-01-26 12:33:53,937 [INFO] iva.lprnet.utils.spec_loader: Merging specification from /workspace/tao-experiments/my_tao_cv_sample/myLprnet/specs/my_spec_scratch.txt
Using TRT engine for inference, setting batch size to the one in eval_config: 1
Producing predictions:   0%|                          | 0/10228 [00:00<?, ?it/s]Traceback (most recent call last):
  File "/root/.cach